In [2]:
import pyodbc
import configparser
import pandas as pd
import numpy as np 
from datetime import datetime, time


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")

# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

#gerar query
query = '''
SELECT 
    e.pdv,
    e.SKU,
    COALESCE(e.SKU_PARA, e.SKU) AS SKU_FINAL,
    e.[ESTOQUE ATUAL],
    e.[ESTOQUE EM TRANSITO],
    e.[PEDIDO PENDENTE],
    d.salescurve AS Curva,
    e.CATEGORIA,
    d.dayswithoutsales AS DiasSemVenda,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
FROM 
    estoque_mar e  
LEFT JOIN draft d 
    ON d.loja_id = e.PDV 
   AND d.code = e.SKU
'''
df0 = pd.read_sql(query, conn)



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_3428\1229765338.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df0 = pd.read_sql(query, conn)


In [3]:
df0['pdv'].value_counts()

pdv
20997    27572
20992    26497
20969    26459
21007    13349
20995    12273
         ...  
23156     1978
24253     1414
24254     1362
24268     1246
24258     1008
Name: count, Length: 80, dtype: int64

In [4]:
query_vendas = '''
SELECT 
	B.PDV, 
	B.SKU,
	B.DESCRICAO,
	SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
	C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
WHERE b.[DATA] > '2024-07-28'
GROUP BY
B.PDV, 
	B.SKU,
	B.DESCRICAO,
	C.Ciclo,
	E.ORIGEM 
'''

dfv0 = pd.read_sql(query_vendas, conn)

conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_3428\1692316838.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfv0 = pd.read_sql(query_vendas, conn)


In [5]:
df=df0

In [6]:
dfv0.head()

PDV    SKU                           DESCRICAO  VENDAS_CICLO    Ciclo
0  20995  57551  DEM EUD DES COL VELVET INSPIRE 4ml           1.0  C202509
1  24255  53742          QDB CLEANSING OIL PRM 30ml           0.0  C202510
2  21277  49010       CBEM SAB BARR  L/MEL 2x80g V7           1.0  C202411
3  22541  49929                    GLAM KIT PINCEIS           2.0  C202414
4  12817  48785     MALBEC DES BDY SPR 100ml V4 PCK          12.0  C202412

In [7]:

# 1. Agrupamento
df_agrupado = dfv0.groupby(['PDV', 'SKU', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_vendas = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_vendas.columns.name = None
df_vendas = df_vendas.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_vendas.head()


PDV   SKU                            DESCRICAO  C202411  C202412  \
0  11201  1004        FLORATTA DES COL MY BLUE 75ml      0.0      0.0   
1  11201  1005     DEM FLORATTA DES COL MY BLUE 4ml      0.0      0.0   
2  11201  1078      MATCH SRUM CAP POS QUIMICA 50ml      0.0      0.0   
3  11201  1296  PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      0.0   
4  11201  1302       PMPCK LILY DES ANTIT AER 2x75g      0.0      0.0   

   C202413  C202414  C202415  C202416  C202417  ...  C202504  C202505  \
0      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202506  C202507  C202508  C202509  C202510  C202511  C202512  C202513  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 23 columns]

In [8]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [9]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
#folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\DRAFT"   # arquivo dos drafts

# Pattern to match all CSV files
#csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
#df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


#df_draft.shape


In [10]:


#Caminho onde estão as subpastas com os arquivos CSV
#pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
#subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

#df_list = []

# Percorre todas as subpastas
#for subpasta in subpastas:
#    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
#    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

#    for arquivo in arquivos:
#        caminho_arquivo = os.path.join(subpasta, arquivo)
#        try:
#            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
#            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
#            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
#            df_list.append(df)
#        except Exception as e:
#            print(f"Erro ao ler o arquivo {arquivo}: {e}")

#if df_list:
#    df_estoque = pd.concat(df_list, ignore_index=True)

#df_estoque['PDV'] = df_estoque['PDV'].astype(str)

#df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

#df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)'''


In [11]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202511\preço BI\TABELA DE PREÇOS (2).xlsx")

c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [12]:
df_bi_preco.columns

Index(['SKU1', 'SKU2', 'Descrição', 'MARCA', 'CATEGORIA', 'LINHA', 'UF',
       'Tipo Preço', 'PC', 'PV'],
      dtype='object')

In [13]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})
df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'SUPERVISOR'])
df_pdv = df_pdv[~df_pdv['CANAL'].isin(['MTZ','LJ'])]
df_pdv = df_pdv[df_pdv['STATUS']!= "INATIVO"]

df_pdv = df_pdv.drop(columns=['STATUS'])




In [14]:
df_pdv['PDV'].value_counts()

PDV
20968    1
20969    1
20970    1
20986    1
20988    1
20989    1
20991    1
20992    1
20993    1
20994    1
20995    1
20996    1
20997    1
20998    1
20999    1
21000    1
21001    1
21278    1
21375    1
21383    1
21495    1
22541    1
23703    1
23704    1
23711    1
23712    1
24255    1
24257    1
24269    1
24293    1
23813    1
Name: count, dtype: int64

In [15]:
df_pdv['MATCH'] = 1

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [16]:
#df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "EUD.csv"]

In [17]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

In [18]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)



In [19]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2430  C202515   2025-10-08 2025-10-28       21  EUDORA 2025-10-08         15   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2430     C2025    C202517               30

In [20]:
filtered_calendario['match'] = 1

In [21]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [24]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202515\tabela promo\Tabela-de-Promocao_C15-1755294384452.xlsx.xlsx",skiprows=1)


In [25]:
df_tabela = df_tabela[df_tabela['Cód. Combo'].isna()]

In [22]:
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
1  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo  Código do Item  \
0           13/10 a 25/10  Não  PERF. FEMININA         NaN           94060   
1                     NaN  Não  PERF. FEMININA         NaN           52107   
2                     NaN  Não  PERF. FEMININA         NaN           50271   
3                     NaN  Não  PERF. FEMININA         NaN           57550   
4                     NaN  Não  PERF. FEMININA         NaN           52943   

   ... 0.34.2 0.35.2  0.2.3  0.25.3  0.28.3  0.3.3  0.32.3  0.34.3  0.35.3  \
0  ...  28.87  29.72    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
1  ...  33.97  34.97    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
2  ...  23.77  24.47    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
3  ...  27.17  27.97    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
4  ...  35.67  36.72    0.2    0.25    0.28    0.3    0.32    0.34    0.35   

   BSO  
0  Sim  
1  Sim  
2  Sim  
3  Sim  
4  Sim  

[5 rows x 47 columns]

In [23]:
df_tabela = df_tabela[[    'Ciclo',                 'Veiculo',
              'Tipo de Promoção',  'Estratégia de Promoção',
                 'Tipo_mecanica', 'Promo Período Limitado?',
                           'EAM',               'Categoria',
                    'Cód. Combo',          'Código do Item',
             'Descrição do Item',     'Chamada Promocional',
                 'Valor do Guia',      'Preço Promocionado',
                 '% de Desconto',           'RE compra por',
                  'RE Vende por',          'RE lucra  (R$)']]

In [24]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)

In [25]:
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
1  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202515    Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
1                     NaN  Não  PERF. FEMININA         NaN          52107   
2                     NaN  Não  PERF. FEMININA         NaN          50271   
3                     NaN  Não  PERF. FEMININA         NaN          57550   
4                     NaN  Não  PERF. FEMININA         NaN          52943   

                                   Descrição do Item  \
0     EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
1     EUDORA DIVA FABULOSA DESODORANTE COLONIA 100ML   
2  EUDORA DESODORANTE COLÔNIA KISS ME NOW 50ml VE...   
3     EUDORA VELVET MILANO DESODORANTE COLÔNIA 100ML   
4        Eudora Magnific Rouge Camélia Des Col 75 ML   

                                 Chamada Promocional  Valor do Guia  \
0  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...         119.90   
1  EUDORA DIVA FABULOSA DESODORANTE COLONIA 100ML...         139.90   
2  EUDORA DESODORANTE COLÔNIA KISS ME NOW 50ml VE...          99.99   
3  EUDORA VELVET MILANO DESODORANTE COLÔNIA 100ML...         119.90   
4  Eudora Magnific Rouge Camélia Des Col 75 ML | ...         134.90   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                84.9          0.292          59.43          84.9   
1                99.9          0.286          69.93          99.9   
2                69.9          0.301          48.93          69.9   
3                79.9          0.334          55.93          79.9   
4               104.9          0.222          73.43         104.9   

   RE lucra  (R$)  
0           25.47  
1           29.97  
2           20.97  
3           23.97  
4           31.47

In [26]:
df_tabela = pd.merge(left=df_tabela,right=df0[['SKU','SKU_FINAL']],left_on='Código do Item',right_on='SKU',how='left')
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
1  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
2  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
3  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
4  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
1           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
2           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
3           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
4           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   

                                Descrição do Item  \
0  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
1  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
2  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
3  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
4  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   

                                 Chamada Promocional  Valor do Guia  \
0  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
1  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
2  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
3  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
4  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                84.9          0.292          59.43          84.9   
1                84.9          0.292          59.43          84.9   
2                84.9          0.292          59.43          84.9   
3                84.9          0.292          59.43          84.9   
4                84.9          0.292          59.43          84.9   

   RE lucra  (R$)    SKU SKU_FINAL  
0           25.47  94060     94060  
1           25.47  94060     94060  
2           25.47  94060     94060  
3           25.47  94060     94060  
4           25.47  94060     94060

In [27]:
df_tabela['Código do Item'] = np.where(df_tabela['SKU_FINAL'].notna(),df_tabela['SKU_FINAL'],df_tabela['Código do Item'])

In [28]:
df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])

In [29]:
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
1  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
2  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
3  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
4  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
1           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
2           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
3           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
4           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   

                                Descrição do Item  \
0  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
1  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
2  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
3  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   
4  EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML   

                                 Chamada Promocional  Valor do Guia  \
0  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
1  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
2  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
3  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   
4  FGCF MOVIMENTO AUTO CUIDADO (13 a 25 OUTUBRO) ...          119.9   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0                84.9          0.292          59.43          84.9   
1                84.9          0.292          59.43          84.9   
2                84.9          0.292          59.43          84.9   
3                84.9          0.292          59.43          84.9   
4                84.9          0.292          59.43          84.9   

   RE lucra  (R$)  
0           25.47  
1           25.47  
2           25.47  
3           25.47  
4           25.47

In [30]:
df_tabela['MATCH'] = 1

In [31]:
df_tabela = pd.merge(left=df_tabela,right=df_pdv[['PDV','MATCH','UF','DESCRIÇÃO PDV','ANALISTA']],on='MATCH',how='inner')

In [32]:
df_tabela.head()

Ciclo    Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
1  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
2  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
3  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   
4  202515  Fora Guia      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
1           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
2           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
3           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   
4           13/10 a 25/10  Não  PERF. FEMININA         NaN          94060   

   ... Preço Promocionado % de Desconto  RE compra por  RE Vende por  \
0  ...               84.9         0.292          59.43          84.9   
1  ...               84.9         0.292          59.43          84.9   
2  ...               84.9         0.292          59.43          84.9   
3  ...               84.9         0.292          59.43          84.9   
4  ...               84.9         0.292          59.43          84.9   

   RE lucra  (R$)  MATCH    PDV  UF      DESCRIÇÃO PDV  ANALISTA  
0           25.47      1  20968  SE   HIB ITABAIANINHA  MARCYARA  
1           25.47      1  20969  AL  HIB MARECHAL DEOD  THAYLLAN  
2           25.47      1  20970  BA   ER SAO SEBASTIAO    DARLIN  
3           25.47      1  20986  BA       HIB OLINDINA     LUCAS  
4           25.47      1  20988  BA      HIB QUEIMADAS    DARLIN  

[5 rows x 23 columns]

In [33]:
df_tabela = df_tabela.drop_duplicates()

In [34]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [35]:
df.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection'],
      dtype='object')

In [36]:
df.head()

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  20998  51213     51213            92                  21             753   
1  20998  83960     83960            10                   5               0   
2  20998  75293     75293             6                   1               0   
3  20998  75888     75888             3                   0               0   
4  20998  52898     52898           341                   0               0   

  Curva     CATEGORIA  DiasSemVenda  nextcycleprojection  \
0     B    PERFUMARIA           1.0                258.0   
1     C  DESODORANTES           4.0                 11.0   
2     B     MAQUIAGEM           3.0                  0.0   
3     C     MAQUIAGEM          27.0                  0.0   
4     B    PERFUMARIA           1.0                 43.0   

   secondtonextcycleprojection  
0                          0.0  
1                          0.0  
2                          0.0  
3                          0.0  
4                          0.0

In [37]:
df['pdv'] = df['pdv'].astype(str)

In [38]:
df['SKU_FINAL'] = df['SKU_FINAL'].astype(str)


In [39]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype('str')

In [40]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [41]:
df_tabela['PDV'] = df_tabela['PDV'].astype(str)

In [42]:
df[['SKU_FINAL','pdv']].head()

SKU_FINAL    pdv
0     51213  20998
1     83960  20998
2     75293  20998
3     75888  20998
4     52898  20998

In [43]:
df[(df['SKU_FINAL']=='93403')]

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO  \
793     20991  93403     93403             0                   1   
10946   20998  93403     93403             0                  15   
35510   20995  93403     93403             0                   0   
45664   20996  93403     93403             0                   0   
53287   21278  93403     93403             0                   0   
73547   20969  93403     93403             0                   0   
77615   20992  93403     93403             0                   0   
92374   20968  93403     93403             0                   0   
92766   21495  93403     93403             0                   0   
107035  20997  93403     93403             0                   0   
109390  24255  93403     93403             0                   0   
117431  22541  93403     93403             0                   1   
393788  21007  93403     93403             0                   0   

       PEDIDO PENDENTE Curva CATEGORIA  DiasSemVenda  nextcycleprojection  \
793                 24     C  INFANTIL           5.0                  0.0   
10946               24     C  INFANTIL           5.0                  0.0   
35510                0     C  INFANTIL          13.0                  0.0   
45664                0     C  INFANTIL           1.0                  0.0   
53287                0     C  INFANTIL           6.0                  0.0   
73547                0     C  INFANTIL          62.0                  0.0   
77615                0     C  INFANTIL           0.0                  0.0   
92374                3     C  INFANTIL           6.0                  0.0   
92766                0     C  INFANTIL           5.0                  0.0   
107035               0     C  INFANTIL           1.0                  0.0   
109390               0     C  INFANTIL           6.0                  0.0   
117431               0     C  INFANTIL           3.0                  0.0   
393788               0  None  INFANTIL           NaN                  NaN   

        secondtonextcycleprojection  
793                             0.0  
10946                           0.0  
35510                           0.0  
45664                           0.0  
53287                           0.0  
73547                           0.0  
77615                           0.0  
92374                           0.0  
92766                           0.0  
107035                          0.0  
109390                          0.0  
117431                          0.0  
393788                          NaN

In [44]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU_FINAL','pdv'],how='right')
df_final.shape  

(10375, 34)

In [45]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU','pdv'],how='right')

In [46]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [47]:
df_final['pdv'] = df_final['PDV']
df_final['SKU_FINAL'] = df_final['Código do Item']

In [48]:
df_final['Descrição do Item']

0       EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML
1       EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML
2       EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML
3       EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML
4       EUDORA VELVET DIVINE DESODORANTE COLÔNIA 100ML
                             ...                      
8923         ESTOJO LA VICTORIE INTENSE NAMORADOS 2025
8924         ESTOJO LA VICTORIE INTENSE NAMORADOS 2025
8925         ESTOJO LA VICTORIE INTENSE NAMORADOS 2025
8926         ESTOJO LA VICTORIE INTENSE NAMORADOS 2025
8927         ESTOJO LA VICTORIE INTENSE NAMORADOS 2025
Name: Descrição do Item, Length: 8928, dtype: object

In [49]:
df_final.head(20)

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0   20968  94060     94060             5                   0               0   
1   20969  94060     94060             1                   0               5   
2   20970  94060     94060            10                   0               0   
3   20986  94060     94060            11                   0               0   
4   20988  94060     94060             9                   0               0   
5   20989  94060     94060            13                   0               0   
6   20991  94060     94060             8                   0              30   
7   20992  94060     94060            10                   0               0   
8   20993  94060     94060            35                   0               0   
9   20994  94060     94060            29                   0               0   
10  20995  94060     94060             0                   0               4   
11  20996  94060     94060             2                   0               0   
12  20997  94060     94060             6                   0              11   
13  20998  94060     94060             0                   0              14   
14  20999  94060     94060            17                   0               0   
15  21000  94060     94060             7                   0               0   
16  21001  94060     94060             7                   0               0   
17  21278  94060     94060             0                   0               0   
18  21375  94060     94060            15                   0               0   
19  21383  94060     94060            13                   0               0   

   Curva   CATEGORIA  DiasSemVenda  nextcycleprojection  ...  \
0      C  PERFUMARIA          12.0                  0.0  ...   
1      C  PERFUMARIA          11.0                  0.0  ...   
2      C  PERFUMARIA           3.0                  0.0  ...   
3      C  PERFUMARIA           0.0                  0.0  ...   
4      C  PERFUMARIA           0.0                  0.0  ...   
5      C  PERFUMARIA           0.0                  0.0  ...   
6      C  PERFUMARIA           6.0                  0.0  ...   
7      C  PERFUMARIA           0.0                  0.0  ...   
8      C  PERFUMARIA           1.0                  0.0  ...   
9      C  PERFUMARIA           4.0                  0.0  ...   
10     C  PERFUMARIA          32.0                  0.0  ...   
11     C  PERFUMARIA           4.0                  0.0  ...   
12     C  PERFUMARIA           0.0                  0.0  ...   
13     C  PERFUMARIA          26.0                  0.0  ...   
14     C  PERFUMARIA           4.0                  0.0  ...   
15     C  PERFUMARIA           0.0                  0.0  ...   
16     C  PERFUMARIA           3.0                  0.0  ...   
17     C  PERFUMARIA          28.0                  0.0  ...   
18     C  PERFUMARIA           0.0                  0.0  ...   
19     C  PERFUMARIA           0.0                  0.0  ...   

    Preço Promocionado  % de Desconto RE compra por RE Vende por  \
0                 84.9          0.292         59.43         84.9   
1                 84.9          0.292         59.43         84.9   
2                 84.9          0.292         59.43         84.9   
3                 84.9          0.292         59.43         84.9   
4                 84.9          0.292         59.43         84.9   
5                 84.9          0.292         59.43         84.9   
6                 84.9          0.292         59.43         84.9   
7                 84.9          0.292         59.43         84.9   
8                 84.9          0.292         59.43         84.9   
9                 84.9          0.292         59.43         84.9   
10                84.9          0.292         59.43         84.9   
11                84.9          0.292         59.43         84.9   
12                84.9          0.292         59.43         84.9   
13                84.9      

In [50]:
df_final['match'] = 1

In [51]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='inner')
df_final.shape

(8928, 40)

In [52]:
df_final.PDV.value_counts()

PDV
20968    288
20969    288
20970    288
20986    288
20988    288
20989    288
20991    288
20992    288
20993    288
20994    288
20995    288
20996    288
20997    288
20998    288
20999    288
21000    288
21001    288
21278    288
21375    288
21383    288
21495    288
22541    288
23703    288
23704    288
23711    288
23712    288
24255    288
24257    288
24269    288
24293    288
23813    288
Name: count, dtype: int64

In [53]:
#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF', 'MARCA', 'ANALISTA']],on = 'PDV',how='inner')
df_final.shape

(8928, 40)

In [54]:
#df_final['SKU'] = df_final['SKU'].astype(str) 
#df_final['PDV'] = df_final['PDV'].astype(str) 
#df_final = pd.merge(left=df_final,right=df_estoque[['SKU_FINAL', 'DDV PREVISTO', 'COBERTURA ATUAL','PDV']],right_on=['PDV','SKU_FINAL'],left_on=['PDV','SKU'],how='left')
#df_final.shape

In [55]:

r'''df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')
df_final.shape  ''' 

"df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) \n\ndf_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')\ndf_final.shape  "

In [56]:
df_final['pdv'].value_counts()

pdv
20968    288
20969    288
20970    288
20986    288
20988    288
20989    288
20991    288
20992    288
20993    288
20994    288
20995    288
20996    288
20997    288
20998    288
20999    288
21000    288
21001    288
21278    288
21375    288
21383    288
21495    288
22541    288
23703    288
23704    288
23711    288
23712    288
24255    288
24257    288
24269    288
24293    288
23813    288
Name: count, dtype: int64

In [57]:
#df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

#df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','SKU'],how='left')
#df_final.shape   

In [58]:
#df_bi_preco = df_bi_preco[df_bi_preco['MARCA']=='EUDORA']

In [59]:
#df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

#df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [60]:
#df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})
#df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

In [61]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio'],
      dtype='object')

In [62]:
#df_final = df_final.drop(columns=['Desativação','Lançamento','Promoção Próximo Ciclo','Compra inteligente semanal/Sugestão de compra','Planograma','Carteira Bloqueada Para Novos Pedidos','Preço Sell In','Quantidade','Item analisado','Promoção Próximo Ciclo + 1','SKU_PARA_VALIDACAO','Ciclo_y'])

In [63]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['SKU_FINAL'].astype(str) 
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU_FINAL'].astype(str)

df_final.shape

(8928, 42)

In [64]:
df_final['PDV']

0       20968
1       20969
2       20970
3       20986
4       20988
        ...  
8923    24255
8924    24257
8925    24269
8926    24293
8927    23813
Name: PDV, Length: 8928, dtype: object

In [65]:
df_final['nextcycleprojection'].value_counts()

df_final['secondtonextcycleprojection'].value_counts()

secondtonextcycleprojection
0.0     4389
1.0       38
3.0       30
2.0       29
4.0       21
6.0       20
5.0       18
19.0      13
10.0      12
49.0       8
27.0       8
9.0        8
18.0       7
34.0       7
32.0       5
37.0       5
8.0        5
30.0       5
7.0        5
17.0       5
94.0       4
69.0       4
11.0       4
52.0       4
53.0       4
98.0       4
14.0       3
56.0       2
15.0       2
13.0       2
20.0       2
44.0       1
24.0       1
67.0       1
23.0       1
51.0       1
28.0       1
41.0       1
54.0       1
29.0       1
16.0       1
36.0       1
31.0       1
12.0       1
33.0       1
55.0       1
Name: count, dtype: int64

In [66]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [67]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'].value_counts()

In [68]:
#df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [69]:
df_final = df_final.rename(columns={'Arquivo_Origem': 'MARCA'})

In [70]:
#df_final = df_final[~df_final['MARCA'].isna()]
#df_final['MARCA'].isna().sum()

In [71]:
df_final = df_final.drop_duplicates()
df_final.shape

(8928, 42)

In [72]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO'],
      dtype='object')

In [73]:
df_vendas['PDV'] = df_vendas['PDV'].astype(str)
df_vendas['SKU'] = df_vendas['SKU'].astype(str)

df_vendas.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513'],
      dtype='object')

In [74]:
df_final.shape

(8928, 42)

In [75]:
df_vendas.head()

PDV   SKU                            DESCRICAO  C202411  C202412  \
0  11201  1004        FLORATTA DES COL MY BLUE 75ml      0.0      0.0   
1  11201  1005     DEM FLORATTA DES COL MY BLUE 4ml      0.0      0.0   
2  11201  1078      MATCH SRUM CAP POS QUIMICA 50ml      0.0      0.0   
3  11201  1296  PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      0.0   
4  11201  1302       PMPCK LILY DES ANTIT AER 2x75g      0.0      0.0   

   C202413  C202414  C202415  C202416  C202417  ...  C202504  C202505  \
0      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202506  C202507  C202508  C202509  C202510  C202511  C202512  C202513  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 23 columns]

In [76]:
df_final = pd.merge(df_final,df_vendas,left_on=['PDV','SKU'],right_on=['PDV','SKU'],how='left')

In [77]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513'],
      dtype='object')

In [78]:
df_final.iloc[:, -18:-1] = df_final.iloc[:, -18:-1].fillna(0)

In [79]:
# Define list of target columns
sales_2024_cols = df_final.columns[-18:-1]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 17CICLOS'] = df_final[sales_2024_cols].max(axis=1)



In [80]:
df_final.head()

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  20968  94060     94060             5                   0               0   
1  20969  94060     94060             1                   0               5   
2  20970  94060     94060            10                   0               0   
3  20986  94060     94060            11                   0               0   
4  20988  94060     94060             9                   0               0   

  Curva   CATEGORIA  DiasSemVenda  nextcycleprojection  ...  C202505  C202506  \
0     C  PERFUMARIA          12.0                  0.0  ...      8.0      0.0   
1     C  PERFUMARIA          11.0                  0.0  ...      5.0      3.0   
2     C  PERFUMARIA           3.0                  0.0  ...      0.0      0.0   
3     C  PERFUMARIA           0.0                  0.0  ...      0.0      0.0   
4     C  PERFUMARIA           0.0                  0.0  ...      0.0      0.0   

  C202507 C202508 C202509 C202510 C202511 C202512 C202513  \
0     0.0     0.0     0.0     0.0     8.0     2.0     0.0   
1     0.0     0.0     0.0     0.0     1.0     3.0     0.0   
2     0.0     0.0     0.0     0.0     0.0     2.0     0.0   
3     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   PICO DE VENDAS 17CICLOS  
0                     11.0  
1                     43.0  
2                      2.0  
3                      0.0  
4                      0.0  

[5 rows x 64 columns]

In [81]:
df_final.PDV.value_counts()

PDV
20968    292
20969    292
20995    292
20996    292
20997    292
20998    292
21278    292
22541    292
21495    291
20991    291
20989    288
20994    288
20988    288
20986    288
20970    288
20999    288
20992    288
20993    288
21000    288
21375    288
21001    288
21383    288
23703    288
23704    288
23711    288
23712    288
24255    288
24257    288
24269    288
24293    288
23813    288
Name: count, dtype: int64

In [82]:
sales_2024_cols

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512'],
      dtype='object')

In [83]:
vendas_6_meses = df_final.columns[-8:-2]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [84]:
df_final.columns[-19]

'C202414'

In [85]:
CRESCIMENTO = (df_final[df_final.columns[-18]].sum() - df_final[df_final.columns[-3]].sum())/df_final[df_final.columns[-18]].sum() 
print(CRESCIMENTO)

df_final['CRESCIMENTO'] = .2

0.7716087836785548


In [86]:
mesmo_ciclo_ano_passado = df_final.columns[-19]
ciclo_ano_passado = df_final.columns[-19:-18].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [87]:
df_final.columns[-19:-18].str.split(" ")[0][-1]

'C202415'

In [88]:
df_final.columns[-21:-3]

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512', 'C202513'],
      dtype='object')

In [89]:
vendas_todos_historicos = df_final.columns[-21:-3]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] <1,df_final['MEDIA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'])


In [90]:
CRESCIMENTO

np.float64(0.7716087836785548)

In [91]:
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    np.ceil(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO']), 
                                    np.ceil(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado]))

In [92]:
#df_final['PV GINSENG'] = np.where(df_final['PV GINSENG']<1, df_final['Projeção Próximo Ciclo + 1'],df_final['PV GINSENG'])

In [93]:
#df_final = df_final.rename(columns={df_final.columns[18]: "C-4", df_final.columns[19]: "C-3",df_final.columns[20]: "C-2",df_final.columns[21]: "C-1"})

In [94]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513', 'PICO DE VENDAS 17CICL

In [95]:
df_final.drop(columns=df_final.columns[-21:-10], inplace=True)

df_final.drop(columns=df_final.columns[-13:-11], inplace=True)


In [96]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = df_final
   

In [97]:
#df_final['Compra inteligente Próximo Ciclo']


In [98]:
#df_final['DDV PREVISTO'] = df_final['DDV PREVISTO'].fillna(0.01)


In [99]:
#df_final_dedup['DDV PREVISTO'] = np.where(
#    df_final_dedup['DDV PREVISTO'] == 0,
#    0.01,
#    df_final_dedup['DDV PREVISTO']
#)


In [100]:
#df_final_dedup['DDV PREVISTO'].value_counts()

In [101]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [102]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [103]:
#df_final_dedup.columns

In [104]:
#df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [105]:
#df_final_dedup = df_final_dedup.rename(columns={'Ciclo_x':'Ciclo'})

In [106]:
df_final_dedup['SUGESTÃO ABTASTECIMENTO	'] = ''
df_final_dedup['VENDAS R$ ABASTECIMENTO'] = ''


In [107]:
#df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [108]:
#df_final_dedup['COB PROJETADA'] = np.where(
#    df_final_dedup['DDV PREVISTO'] != 0,
#    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
#    999)


In [109]:
#df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL','Projeção Próximo Ciclo + 1',
#                             'CRESCIMENTO'],inplace=True)

In [110]:
#df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [111]:
#df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [112]:
#df_final_dedup.columns

In [113]:
#marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
#marca_promo

In [114]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202415', 'C202510',
       'C202511', 'C202512', 'C202513', 'PICO DE VENDAS 17CICLOS',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t',
  

In [115]:
# Passo 1: ordenar
df_sorted = df_final.sort_values(by='% de Desconto', ascending=False)

# Passo 2: obter até 3 chamadas promocionais por grupo
promo_grouped = (
    df_sorted.groupby(['SKU_FINAL', 'PDV'])['Chamada Promocional']
    .apply(lambda x: x.dropna().unique()[:3])
    .apply(pd.Series)
    .rename(columns={0: 'MECÂNICA 1', 1: 'MECÂNICA 2', 2: 'MECÂNICA 3'})
    .reset_index()
)

# Passo 3: base com maior % de desconto
df_base = df_sorted.drop_duplicates(subset=['SKU_FINAL', 'PDV'], keep='first').reset_index(drop=True)

# Passo 4: merge com chamadas pivotadas
df_merged = df_base.merge(promo_grouped, on=['SKU_FINAL', 'PDV'], how='left')

# Corrigir dicionário: agrupar e pegar o primeiro valor válido por (SKU_FINAL, PDV)
# Passo 1: dicionário com Cód. Combo único por SKU_FINAL+PDV
cod_combo_map = (
    df_final
    .dropna(subset=['Cód. Combo'])
    .groupby(['SKU_FINAL', 'PDV'])['Cód. Combo']
    .first()
    .to_dict()
)

# Passo 2: gerar Series com os valores mapeados
cod_combo_series = df_merged.set_index(['SKU_FINAL', 'pdv']).index.map(cod_combo_map)

# Passo 3: substituir os valores diretamente
df_merged['Cód. Combo'] = cod_combo_series.where(cod_combo_series.notna(), df_merged['Cód. Combo'])



In [116]:
df_merged.PDV.value_counts()

PDV
20986    196
20991    196
23712    196
23711    196
23704    196
23703    196
22541    196
21495    196
21383    196
21375    196
21278    196
21001    196
24269    196
23813    196
24255    196
24257    196
24293    196
20970    196
20969    196
20968    196
20999    196
21000    196
20996    196
20995    196
20997    196
20998    196
20989    196
20994    196
20992    196
20993    196
20988    196
Name: count, dtype: int64

# Columns to bring up front
priority_cols = [
    'PDV_SKU',	'SKU',	'MARCA','INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO','dias_ate_inicio',	
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição','MECÂNICA 1',
       'MECÂNICA 2', 'MECÂNICA 3','Estoque Atual',	'COBERTURA ATUAL',
    'Estoque em Transito',	'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_merged.columns if col not in priority_cols]

# Reorder
df_merged = df_merged[priority_cols + other_cols]


In [117]:
df_merged['INICIO CICLO'] = pd.to_datetime(df_merged['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_merged['FIM CICLO'] = pd.to_datetime(df_merged['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [118]:
df_merged.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202415', 'C202510',
       'C202511', 'C202512', 'C202513', 'PICO DE VENDAS 17CICLOS',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t',
  

In [119]:
df_merged = df_merged.loc[:, ~df_merged.columns.str.endswith('_y')]


In [120]:
df_merged.columns = df_merged.columns.str.replace('_x$', '', regex=True)


In [121]:
df_merged['DESCRICAO'] = df_merged['Descrição do Item']

In [122]:
df_merged['SKU'] = np.where(df_merged['SKU'].isna(),df_merged['SKU_FINAL'],df_merged['SKU'])

In [123]:
df_merged = df_merged.drop(columns=['Veiculo',	'Tipo de Promoção',	'Estratégia de Promoção','Tipo_mecanica'
                                    ,'Chamada Promocional','MATCH','match','Descrição do Item','CRESCIMENTO',
                                    'Cód. Combo'])

In [124]:
df_merged = df_merged.drop(columns=['Código do Item','PDV','RE compra por',	'RE Vende por',	'RE lucra  (R$)','INICIO CICLO',
                                    'FIM CICLO','Ciclo','CATEGORIA','ANALISTA','dias_ate_inicio','PDV_SKU','UFPRODUTO',
                                    'VENDAS R$ ABASTECIMENTO','DURAÇÃO','MEDIANA DO HISTÓRICO','DURAÇÃO'])

In [125]:
df_merged = df_merged.rename(columns={'nextcycleprojection':'PROJEÇÃO PROX CICLO'	,'secondtonextcycleprojection':'PROJEÇÃO PROX CICLO +1'})

In [126]:
df_merged.columns = df_merged.columns.str.upper()

In [127]:
#df_merged = df_merged[['UF','PDV','DESCRIÇÃO PDV','SKU','DESCRICAO','EAM','CATEGORIA','CURVA','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DIASSEMVENDA','PROJEÇÃO PROX CICLO','PROJEÇÃO PROX CICLO +1','PROMO PERÍODO LIMITADO?','VALOR DO GUIA','PREÇO PROMOCIONADO','% DE DESCONTO','PICO DE VENDAS 17CICLOS','PICO VENDAS ULTIMOS 6 CICLOS','MEDIA DO HISTÓRICO']]

In [128]:
df_merged['MEDIA DO HISTÓRICO'] = round(df_merged['MEDIA DO HISTÓRICO'],0)

In [129]:
df_merged[df_merged.columns[19:26]] = df_merged[df_merged.columns[19:26]].fillna(0)

In [130]:
# Colunas que devem estar na frente
colunas_inicio = [
    'UF', 'PDV', 'DESCRIÇÃO PDV', 'SKU', 'DESCRICAO', 'EAM', 'CATEGORIA', 'CURVA',
    'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DIASSEMVENDA',
    'PROJEÇÃO PROX CICLO', 'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?',
    'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO',
    'PICO DE VENDAS 17CICLOS', 'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO'
]

# Colunas que devem estar no fim
colunas_fim = [
    'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t'
]

# Todas as outras colunas (não estão nem no início nem no fim)
colunas_meio = [col for col in df_merged.columns if col not in colunas_inicio + colunas_fim]

# Reordena o DataFrame
df_merged = df_merged[colunas_inicio + colunas_meio + colunas_fim]


In [131]:
df_merged = df_merged.drop_duplicates()

In [132]:
hoje=datetime.today().strftime('%Y-%m-%d')
hoje

'2025-09-03'

In [134]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\EUD_promoção_{ciclo_mais2}_{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_merged.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL